In [1]:
import requests
import pandas as pd
from bs4 import BeautifulSoup
from tqdm import tqdm
import re
import json
import csv

In [2]:
# Raw HTTP headers as a multi-line string
headers = """content-type: text/html;charset=utf-8
server: Apache
content-security-policy: upgrade-insecure-requests; frame-ancestors 'self'
permissions-policy: accelerometer=(), camera=(), gyroscope=(), magnetometer=(), microphone=(), usb=()
expect-ct: max-age=0
referrer-policy: same-origin
x-content-type-options: nosniff
x-xss-protection: 1; mode=block
x-frame-options: SAMEORIGIN
x-permitted-cross-domain-policies: none
expires: Thu, 01 Dec 1994 16:00:00 GMT
cache-control: no-cache,no-store,must-revalidate
content-security-policy: script-src 'self' 'unsafe-inline' 'unsafe-eval'  https://consent.cookiebot.com https://consentcdn.cookiebot.com https://www.googletagmanager.com https://cdn.scarabresearch.com https://jsctool.com https://ajax.googleapis.com https://myclipster.com https://trck.netto-online.de https://trck.marktkauf.de https://www.google-analytics.com https://push.marpu.de https://www.usemaxserver.de https://bat.bing.com https://www.googleadservices.com https://googleads.g.doubleclick.net https://maps.googleapis.com https://mycliplister.com https://www.google.com https://www.gstatic.com https://static.userback.io https://uat.peerius.com https://app.onlim.com https://s.go-mpulse.net https://connect.facebook.net https://netto.peerius.com https://www.googletagmanager.com https://*.clarity.ms https://nettomarkenprod.peerius.episerver.net https://applepay.cdn-apple.com https://pay.google.com https://h.online-metrix.net;base-uri 'self' https://app.onlim.com;object-src 'self';img-src https://www.netto-online.de https://vvv.netto-online.de https://media.netto-online.de https://media.marktkauf.de data: 'self' https://www.google-analytics.com https://bat.bing.com https://www.usemaxserver.de https://push.marpu.de https://www.google.de https://www.google.com https://file.marpu.de https://9398189.fls.doubleclick.net https://maps.gstatic.com https://maps.googleapis.com https://www.econda-monitor.de https://app.onlim.com https://facebook.com https://dacodi-production.s3.amazonaws.com https://mycliplister.com https://*.mycliplister.com https://www.facebook.com https://*.clarity.ms https://www.googletagmanager.com https://*.bing.com https://*.gstatic.com https://h.online-metrix.net;
x-frame-options: SAMEORIGIN
accept-ranges: bytes
x-akamai-transformed: 9 1528884 0 pmb=mTOE,1mRUM,1
vary: Accept-Encoding
content-encoding: gzip
date: Thu, 21 Dec 2023 12:02:01 GMT
set-cookie: cc-hrusEClWn70AAAFb65Fb7Vz2=wfYKAQNIym4AAAGMfG4QA4v4; Max-Age=1728000; Expires=Wed, 10-Jan-2024 12:02:00 GMT; Path=/; Secure; HttpOnly;HttpOnly;Secure;HttpOnly;Secure;SameSite=none
server-timing: cdn-cache; desc=MISS
server-timing: edge; dur=83
server-timing: origin; dur=1108
strict-transport-security: max-age=86400
set-cookie: bm_sv=604D33FEA10EB1D959E9991F3FBB23F2~YAAQkmAYuOlKoVmMAQAAAQhBjBZiKbjnA1nLVUJK7jCilY4Y5nnsigLWFeSSJbsDh/S2rwZGqmstTwmgXW1pVfzG7UiKbual5Nprj1RjBYPG5bOwIdIz4ZjezIbtD0c9LO9XBnJOqYSjID3Pl9bjc09AJNvd+Oufiekvrnnz7z5Z71RP+/LqOoyOKN3iKiDzGMGoSMQ3gct3SeDP/FONS+RMsX0jg+G/zJyuRIhkTFf8cb8X+gkdVAaqBFfPXFFaDGB9g7LJ~1; Domain=.netto-online.de; Path=/; Expires=Thu, 21 Dec 2023 12:42:44 GMT; Max-Age=2443; Secure
server-timing: ak_p; desc="1703160120005_3088605330_196247845_119106_12896_1_0_41";dur=1
X-Firefox-Spdy: h2""".split('\n')

# Split the headers string into individual header lines and create a dictionary
headers = {a.split(':')[0]:a.replace(a.split(':')[0] + ': ', '') for a in headers}

In [3]:
all_links = []
# Loop through pages and extract product links
for p in tqdm(range(0, 30)):
    url = 'https://www.netto-online.de/lebensmittel/c-N01/' + str(p)
    resp = requests.get(url, headers=headers)
    
    if resp.status_code == 200:
        soup = BeautifulSoup(resp.text, 'html.parser')
        
        # Find all product divs
        products = soup.find_all('div', class_='product')
        
        # Extract the product links
        for product in products[:60]:  # Adjusted to match your requirement
            link = product.find('a', class_='product__content')
            if link and 'href' in link.attrs:
                all_links.append(link['href'])
    else:
        print(f"Failed to retrieve the page {p}: Status code {resp.status_code}")

# Print or process the collected links
for link in all_links:
    print(link)

100%|██████████| 30/30 [00:58<00:00,  1.94s/it]

https://www.netto-online.de/kitkat-lion-box-2-801-kg/p-2192205000?GTMList=Lebensmittel+%2F+Content-Kachel+Spirituosen
https://www.netto-online.de/mueller-thurgau-qualitaetswein-trocken-11-0-vol-1-liter/p-1843995000?GTMList=Lebensmittel+%2F+Content-Kachel+Spirituosen
https://www.netto-online.de/biobio-h-vollmilch-3-8-1-liter-12er-pack/p-2204525000?GTMList=Lebensmittel+%2F+Content-Kachel+Spirituosen
https://www.netto-online.de/biobio-weizenmehl-typ-550-1-kg-10er-pack/p-2163762000?GTMList=Lebensmittel+%2F+Content-Kachel+Spirituosen
https://www.netto-online.de/bier-maxx-bierzapfanlage-mit-co2-kapsel-60w/p-2634210000?GTMList=Lebensmittel+%2F+Content-Kachel+Spirituosen
https://www.netto-online.de/coffeeb-by-caf-royal-ristretto-9-coffee-balls-51g-10er-pack/p-2586744000?GTMList=Lebensmittel+%2F+Content-Kachel+Spirituosen
https://www.netto-online.de/italienischer-weisswein-9-5-vol-1-5-liter-8er-pack/p-2435836000?GTMList=Lebensmittel+%2F+Content-Kachel+Spirituosen
https://www.netto-online.de/dor

In [4]:
all_attrs = []  # Initialize an empty list to store all extracted attributes

# Iterate over all_links using tqdm for progress visualization
for l in tqdm(all_links):
    attrs = {}  # Initialize an empty dictionary for storing attributes for each link

    attrs['Artikelinformationen'] = ''  # Initialize 'Artikelinformationen' attribute as an empty string

    # Send GET request to the URL l with custom headers
    resp = requests.get(l, headers=headers)
    
    # Parse the HTML content of the response
    soup = BeautifulSoup(resp.text)

    # Extract 'id' attribute from the page
    attrs['id'] = soup.find(class_='artikel-number').text.replace('Artikelnummer:', '').strip()

    # Extract 'name' attribute from the page
    attrs['name'] = soup.find('h1').text.strip()

    # Attempt to extract 'brand' attribute from the page
    try:
        attrs['brand'] = [a_tag.get("href").rsplit('/', 1)[-1] for div in soup.find_all("div", class_="detail-page__common-infos__title__rating-brand") if (a_tag := div.find("a")) is not None][0]
    except:
        pass  # Ignore if extraction fails

    # Attempt to extract 'ingredients' attribute from the page
    try:
        attrs['ingredients'] = [re.sub(r'[\s]+', ' ', element.get_text().split('Zutatenverzeichnis: ')[1].strip())
                                for element in soup.find(class_='food-labeling').find_all(class_='food-labeling__text') 
                                if 'Zutatenverzeichnis' in element.get_text()][0]
    except:
        pass  # Ignore if extraction fails

    # Attempt to extract 'ingredients' attribute from the page (alternative label)
    try:
        attrs['ingredients'] = [re.sub(r'[\s]+', ' ', element.get_text().split('Inhaltsstoffe: ')[1].strip()) 
                                for element in soup.find(class_='food-labeling').find_all(class_='food-labeling__text')
                                if 'Inhaltsstoffe' in element.get_text()][0]
    except:
        pass  # Ignore if extraction fails

    # Attempt to extract 'category' attribute from the page
    try:
        attrs['category'] = [cat.text.strip() for cat in soup.find_all("a", class_="breadcrumb__item__link breadcrumb__item__link--underline")][1]
    except:
        pass  # Ignore if extraction fails

    # Attempt to extract 'sub-category' attribute from the page
    try:
        attrs['sub-category'] = [cat.text.strip() for cat in soup.find_all("a", class_="breadcrumb__item__link breadcrumb__item__link--underline")][2]
    except:
        pass  # Ignore if extraction fails

    # Attempt to extract 'allergens' attribute from the page
    try:
        attrs['allergens'] = [re.sub(r'[\s]+', ' ', element.get_text().split('Enthaltene Allergene: ')[1].strip())
                            for element in soup.find(class_='food-labeling').find_all(class_='food-labeling__text') 
                            if 'Enthaltene Allergene' in element.get_text()][0]
    except:
        pass  # Ignore if extraction fails

    attrs['labels'] = ''  # Initialize 'labels' attribute as an empty string

    # Attempt to extract additional tables under 'food-labeling' for attributes
    try:
        for table in soup.find(class_='food-labeling').find_all(class_='food-labeling__table-wrapper'):
            result_string = ''
            for row in table.find('table').find_all('tr'):
                columns = row.find_all('td')
                row_data = [col.text.strip() for col in columns]
                result_string += '->'.join(row_data) + '. '

            # Remove the last dot and space, then add a dot at the end
            result_string = result_string.rstrip('. ')

            attrs[table.find('p').text] = result_string  # Add attribute extracted from the table
    except:
        pass  # Ignore if extraction fails

    # Extract 'image-link' attribute from the page
    attrs['image-link'] = soup.find(class_='productImage scale-img').attrs['src']

    # Attempt to extract 'description' attribute from the page
    try:
        attrs['description'] = re.sub(r'[\s]+', ' ', soup.find(class_='tc-product-description').text.strip())
    except:
        pass  # Ignore if extraction fails

    # Determine if the product is on sale and extract related attributes
    if soup.find(class_='product__old-price'):
        attrs['on-sale'] = True
        attrs['sale-price'] = soup.find(class_='prices__ins--digits-before-comma').text.strip().replace('*', '')
        attrs['price'] = soup.find('del', class_='product__old-price').text.split('\n')[1].strip()
    elif soup.find(class_='prices__ins--digits-before-comma'):
        attrs['on-sale'] = False
        attrs['price'] = soup.find(class_='prices__ins--digits-before-comma').text.strip().replace('*', '')

    # Attempt to extract 'unit-price' attribute from the page
    try:
        for prop in soup.find_all(class_='product-property'):
            if prop.find(class_='product-property__label').text.strip() == "Grundpreis:":
                attrs['unit-price'] = prop.find(class_='product-property__value').text.replace('\n', '').strip()
    except:
        pass  # Ignore if extraction fails

    # Attempt to extract additional 'Artikelinformationen' attribute from the page
    try:
        for a in soup.find(class_='food-labeling').find_all(class_='food-labeling__text'):
            if 'Zutatenverzeichnis' not in a.text and "Enthaltene Allergene" not in a.text:
                attrs['Artikelinformationen'] += (re.sub(r'[\s]+', ' ', a.text.strip() + ' ')).rstrip(' ')
    except:
        pass  # Ignore if extraction fails

    # Attempt to extract 'rating' attribute from the page
    try:
        attrs['rating'] = (lambda match: match.group(1) if match else None)(re.search(r'rating-(\d+)-full', ' '.join(soup.find(class_="product__rating").find('div', class_='rating').get('class'))))
    except:
        pass  # Ignore if extraction fails

    attrs['link'] = l  # Store the current link in the attributes dictionary

    all_attrs.append(attrs)  # Append the extracted attributes dictionary to the list

# Return the list containing all extracted attributes for each link
all_attrs


100%|██████████| 1651/1651 [46:55<00:00,  1.71s/it] 


[{'Artikelinformationen': 'Bezeichnung Lebensmittel: KitKat Chunky White: Knusperwaffel mit weißer Schokolade. Lion: Waffel mit Karamell und Knuspergetreide. KitKat: Knusperwaffel in Milchschokolade. KitKat Chunky: Knusperwaffel in Milchschokolade. Lion White: Gefüllte Waffel mit Karamell und Weizencerealien, überzogen mit weißer Fettglasur. KitKat Chunky Peanut Butter: Knusperwaffel überzogen mit Erdnusscreme in Milchschokolade.Verantwortlicher Lebensmittelunternehmer: Nestlé Deutschland AG, 60523 Frankfurt am Main',
  'id': '2192205000',
  'name': 'KitKat & Lion Box 2.801 kg',
  'brand': 'kitkat',
  'category': 'Süßigkeiten',
  'sub-category': 'Schokoriegel',
  'labels': '',
  'image-link': 'https://media.netto-online.de/products/2192/205/000/2192205000_prod_001?im=Resize=(450,450),type=downsize,aspect=fit;Crop,size=(450,450),gravity=Center,allowExpansion;BackgroundColor,color=ffffff;UnsharpMask,gain=1.0,threshold=0.05;',
  'description': "KitKat Box in verschiedenen Sorten im clever

In [5]:
######################################### TO COMBINE Nährwertangaben & Vitamin / Mineral keys ###############################################

# Iterate over each dictionary (item) in the all_attrs list
for item in all_attrs:
    # Check if both 'Nährwertangaben' and 'Vitamin / Mineral' keys exist in the current dictionary (item)
    if 'Nährwertangaben' in item and 'Vitamin / Mineral' in item:
        # Combine the values of 'Nährwertangaben' and 'Vitamin / Mineral' with a period and space in between
        item['nutriments'] = item['Nährwertangaben'] + '. ' + item['Vitamin / Mineral']
        
        # Delete the 'Nährwertangaben' key from the dictionary
        del item['Nährwertangaben']
        
        # Delete the 'Vitamin / Mineral' key from the dictionary
        del item['Vitamin / Mineral']


In [6]:
###################################### TO APPEND Artikelinformationen's values TO THE description key #############################################

for item in all_attrs:
    if 'description' in item and 'Artikelinformationen' in item:
        # Append Artikelinformationen value to Description
        item['description'] = item.get('description', '') + ' ' + item.get('Artikelinformationen', '')
        # Delete the Artikelinformationen key
        del item['Artikelinformationen']

In [7]:
################################################### TO RE-ORDER THE KEY'S PLACE #####################################################

for attr in all_attrs:
    if 'nutriments' in attr:
        # Find the index of 'labels' key in the dictionary
        labels_index = list(attr.keys()).index('labels')
        
        # Move 'nutriments' key to after 'labels'
        attr['nutriments'] = attr.pop('nutriments')
        
        # Convert dictionary items to a list of tuples
        attr_items = list(attr.items())
        
        # Remove the last item (which is now 'nutriments') and insert it after 'labels'
        attr_items.insert(labels_index + 1, attr_items.pop(-1))
        
        # Clear the dictionary
        attr.clear()
        
        # Update the dictionary with the re-ordered list of tuples
        attr.update(attr_items)


In [8]:
############################################# SAVING FOOD PRODUCTS IN A .JSON FILE ################################################

with open('netto_food_products.json', 'w', encoding='utf-8') as json_file:
    json.dump(all_attrs, json_file, ensure_ascii=False, indent=4)

In [9]:
######################################## THIS IS A TRIAL FOR A SINGLE PRODUCT ###############################################


# l = "https://www.netto-online.de/torre-santa-primitivo-puglia-igt-13-0-vol-0-75-liter/p-1843947000?GTMList=Lebensmittel+%2F+Content-Kachel+Spirituosen"

# all_attrs = []
# attrs = {}
# attrs['Artikelinformationen'] = ''
# resp = requests.get(l, headers=headers)
# soup = BeautifulSoup(resp.text)
# attrs['id'] = soup.find(class_='artikel-number').text.replace('Artikelnummer:', '').strip()
# attrs['name'] = soup.find('h1').text.strip()

# try:
#     attrs['brand'] = [a_tag.get("href").rsplit('/', 1)[-1] for div in soup.find_all("div", class_="detail-page__common-infos__title__rating-brand") if (a_tag := div.find("a")) is not None][0]
# except:
#     pass

# try:
#     attrs['ingredients'] = [re.sub(r'[\s]+', ' ', element.get_text().split('Zutatenverzeichnis: ')[1].strip())
#         for element in soup.find(class_='food-labeling').find_all(class_='food-labeling__text') 
#             if 'Zutatenverzeichnis' in element.get_text()][0]
# except:
#     pass

# try:
#     attrs['ingredients'] = [re.sub(r'[\s]+', ' ', element.get_text().split('Inhaltsstoffe: ')[1].strip()) 
#         for element in soup.find(class_='food-labeling').find_all(class_='food-labeling__text')
#             if 'Inhaltsstoffe' in element.get_text()][0]
# except:
#     pass

# try:
#     attrs['category'] =  [cat.text.strip() for cat in soup.find_all("a", class_="breadcrumb__item__link breadcrumb__item__link--underline")][1]
# except:
#     pass

# try:
#     attrs['sub-category'] = [cat.text.strip() for cat in soup.find_all("a", class_="breadcrumb__item__link breadcrumb__item__link--underline")][2]
# except:
#     pass

# try:
#     attrs['allergens'] = [re.sub(r'[\s]+', ' ', element.get_text().split('Enthaltene Allergene: ')[1].strip())
#                 for element in soup.find(class_='food-labeling').find_all(class_='food-labeling__text') 
#                     if 'Enthaltene Allergene' in element.get_text()][0]
# except:
#     pass

# attrs['labels'] = ''

# try:
#     for table in soup.find(class_='food-labeling').find_all(class_='food-labeling__table-wrapper'):
#         result_string = ''
#         for row in table.find('table').find_all('tr'):
#             columns = row.find_all('td')
#             row_data = [col.text.strip() for col in columns]
#             result_string += '->'.join(row_data) + '. '

#         # Remove the last dot and space, then add a dot at the end
#         result_string = result_string.rstrip('. ')

#         attrs[table.find('p').text] = result_string
# except:
#     pass

# attrs['image-link'] = soup.find(class_= 'productImage scale-img').attrs['src']

# try:
#     attrs['description'] = re.sub(r'[\s]+', ' ', soup.find(class_='tc-product-description').text.strip())
# except:
#     pass

# if soup.find(class_='product__old-price'):
#     attrs['on-sale'] = True
#     attrs['sale-price'] = soup.find(class_='prices__ins--digits-before-comma').text.strip().replace('*', '')
#     attrs['price'] = soup.find('del', class_='product__old-price').text.split('\n')[1].strip()
# elif soup.find(class_='prices__ins--digits-before-comma'):
#     attrs['on-sale'] = False
#     attrs['price'] = soup.find(class_='prices__ins--digits-before-comma').text.strip().replace('*', '')


# try:
#     for prop in soup.find_all(class_='product-property'):
#         if prop.find(class_='product-property__label').text.strip() == "Grundpreis:":
#             attrs['unit-price'] = prop.find(class_='product-property__value').text.replace('\n', '').strip()
# except:
#     pass

# try:
#     for a in soup.find(class_='food-labeling').find_all(class_='food-labeling__text'):
#             if 'Zutatenverzeichnis' not in a.text and "Enthaltene Allergene" not in a.text:
#                 attrs['Artikelinformationen'] += (re.sub(r'[\s]+', ' ', a.text.strip() + ' ')).rstrip(' ')
# except:
#     pass

# try:
#     attrs['rating'] = (lambda match: match.group(1) if match else None)(re.search(r'rating-(\d+)-full', ' '.join(soup.find(class_="product__rating").find('div', class_='rating').get('class'))))
# except:
#     pass

# attrs['link'] = l
# all_attrs.append(attrs)

# all_attrs

In [10]:
all_links_cosmetic = []
# Loop through pages and extract product links
for p in tqdm(range(0, 28)):
    url = 'https://www.netto-online.de/drogerie/c-N02/' + str(p)
    resp = requests.get(url, headers=headers)
    
    if resp.status_code == 200:
        soup = BeautifulSoup(resp.text, 'html.parser')
        
        # Find all product divs
        products = soup.find_all('div', class_='product')
        
        # Extract the product links
        for product in products[:60]:  # Adjusted to match your requirement
            link = product.find('a', class_='product__content')
            if link and 'href' in link.attrs:
                all_links_cosmetic.append(link['href'])
    else:
        print(f"Failed to retrieve the page {p}: Status code {resp.status_code}")

# Print or process the collected links
for link in all_links_cosmetic:
    print(link)

100%|██████████| 28/28 [00:53<00:00,  1.91s/it]

https://www.netto-online.de/ticksafe-rotierender-zeckengreifer-mensch-16-9cm-weiss-gelb/p-2657091000
https://www.netto-online.de/ticksafe-rotierender-zeckengreifer-tier-16-9cm-tuerkis-weiss/p-2657090000
https://www.netto-online.de/soumm-roll-on-anti-transpirant-50-ml-versch-sorten/p-2130458001
https://www.netto-online.de/vitalmaxx-schall-zahnbuerste-360-automatisch-2-0/p-2658585000
https://www.netto-online.de/bideo-reinigungsmittel-wc-intensivschaum-1-5kg/p-2658588000
https://www.netto-online.de/cleanmaxx-spray-mopp-mit-600ml-tank-tuerkis/p-1913650000
https://www.netto-online.de/vitalmaxx-shiatsu-massagegeraet-nacken-schulter-3-tlg-6v-grau-tuerkis/p-2313729000
https://www.netto-online.de/vitalmaxx-hornhautentferner-mit-saugfunktion/p-2125851000
https://www.netto-online.de/vitalmaxx-haarentferner-nano-glas-7x10-5cm-lila/p-2482640000
https://www.netto-online.de/vitalmaxx-mini-massage-gun-smart-grip/p-2507413000
https://www.netto-online.de/favora-kuechentuecher-3-lagig-4-x-64-blatt/p-2229

In [13]:
all_attrs_cosmetic = []

# Iterate through all the cosmetic product links
for l in tqdm(all_links_cosmetic):
    attrs = {}  # Dictionary to store the attributes of each product
    attrs['Artikelinformationen'] = ''
    
    # Send a GET request to fetch the content of the product page
    resp = requests.get(l, headers=headers)
    # Parse the response text using BeautifulSoup
    soup = BeautifulSoup(resp.text)
    
    # Extract product ID
    try:
        attrs['id'] = soup.find(class_='artikel-number').text.replace('Artikelnummer:', '').strip()
    except:
        pass
    
    # Extract product name
    try:
        attrs['name'] = soup.find('h1').text.strip()
    except:
        pass

    # Extract product brand
    try:
        attrs['brand'] = [a_tag.get("href").rsplit('/', 1)[-1] for div in soup.find_all("div", class_="detail-page__common-infos__title__rating-brand") if (a_tag := div.find("a")) is not None][0]
    except:
        pass

    # Extract ingredients using two different possible labels
    try:
        attrs['ingredients'] =[re.sub(r'[\s]+', ' ', element.get_text().split('Zutatenverzeichnis: ')[1].strip())
            for element in soup.find(class_='food-labeling').find_all(class_='food-labeling__text') 
                if 'Zutatenverzeichnis' in element.get_text()][0]
    except:
        pass

    try:
        attrs['ingredients'] = [re.sub(r'[\s]+', ' ', element.get_text().split('Inhaltsstoffe: ')[1].strip()) 
            for element in soup.find(class_='food-labeling').find_all(class_='food-labeling__text')
                if 'Inhaltsstoffe' in element.get_text()][0]
    except:
        pass

    # Extract product category
    try:
        attrs['category'] =  [cat.text.strip() for cat in soup.find_all("a", class_="breadcrumb__item__link breadcrumb__item__link--underline")][1]
    except:
        pass

    # Extract product sub-category
    try:
        attrs['sub-category'] = [cat.text.strip() for cat in soup.find_all("a", class_="breadcrumb__item__link breadcrumb__item__link--underline")][2]
    except:
        pass

    # Extract allergens information
    try:
        attrs['allergens'] = [re.sub(r'[\s]+', ' ', element.get_text().split('Enthaltene Allergene: ')[1].strip())
                    for element in soup.find(class_='food-labeling').find_all(class_='food-labeling__text') 
                        if 'Enthaltene Allergene' in element.get_text()][0]
    except:
        pass

    # Initialize 'labels' as an empty string
    attrs['labels'] = ''

    # Extract and format nutritional or other tabular information
    try:
        for table in soup.find(class_='food-labeling').find_all(class_='food-labeling__table-wrapper'):
            result_string = ''
            for row in table.find('table').find_all('tr'):
                columns = row.find_all('td')
                row_data = [col.text.strip() for col in columns]
                result_string += '->'.join(row_data) + '. '
            
            # Remove the last dot and space, then add a dot at the end
            result_string = result_string.rstrip('. ')

            attrs[table.find('p').text] = result_string
    except:
        pass

    # Extract the image link of the product
    try:
       attrs['image-link'] = soup.find(class_= 'productImage scale-img').attrs['src']
    except:
        pass

    # Extract product description
    try:
        attrs['description'] = re.sub(r'[\s]+', ' ', soup.find(class_='tc-product-description').text.strip())
    except:
        pass

    # Extract price and sale information
    try:
        if soup.find(class_='product__old-price'):
            attrs['on-sale'] = True
            attrs['sale-price'] = soup.find(class_='prices__ins--digits-before-comma').text.strip().replace('*', '')
            attrs['price'] = soup.find('del', class_='product__old-price').text.split('\n')[1].strip()
        elif soup.find(class_='prices__ins--digits-before-comma'):
            attrs['on-sale'] = False
            attrs['price'] = soup.find(class_='prices__ins--digits-before-comma').text.strip().replace('*', '')
    except:
        pass

    # Extract unit price if available
    try:
        for prop in soup.find_all(class_='product-property'):
            if prop.find(class_='product-property__label').text.strip() == "Grundpreis:":
                attrs['unit-price'] = prop.find(class_='product-property__value').text.replace('\n', '').strip()
    except:
        pass

    # Extract any additional information that does not fit into other categories
    try:
        for a in soup.find(class_='food-labeling').find_all(class_='food-labeling__text'):
                if 'Zutatenverzeichnis' not in a.text and "Enthaltene Allergene" not in a.text:
                    attrs['Artikelinformationen'] += (re.sub(r'[\s]+', ' ', a.text.strip() + ' ')).rstrip(' ')
    except:
        pass

    # Extract product rating if available
    try:
        attrs['rating'] = (lambda match: match.group(1) if match else None)(re.search(r'rating-(\d+)-full', ' '.join(soup.find(class_="product__rating").find('div', class_='rating').get('class'))))
    except:
        pass

    # Store the link of the product page
    attrs['link'] = l

    # Append the extracted attributes to the list of all attributes
    all_attrs_cosmetic.append(attrs)

# The final list of all attributes
all_attrs_cosmetic


100%|██████████| 1614/1614 [37:52<00:00,  1.41s/it] 


[{'Artikelinformationen': '',
  'id': '2657091000',
  'name': 'ticksafe rotierender Zeckengreifer Mensch 16,9cm weiß/gelb',
  'category': 'Die Höhle der Löwen',
  'sub-category': 'Alle Löwen Deals',
  'labels': '',
  'image-link': 'https://media.netto-online.de/products/2657/091/000/2657091000_prod_001?im=Resize=(450,450),type=downsize,aspect=fit;Crop,size=(450,450),gravity=Center,allowExpansion;BackgroundColor,color=ffffff;UnsharpMask,gain=1.0,threshold=0.05;',
  'description': 'Zecken sind echte Plagegeister für Mensch und Tier und sollten nach einem Stich zeitnah und richtig entfernt werden. Der tickSAFE Zeckengreifer hat sich seit Jahren als zuverlässiger Helfer zur sanften Entfernung von Zecken bewährt. Mit seinem flexiblen Greiferkopf vermindert er das Risiko die Zecke beim Entfernen zu quetschen. Während Pinzetten & Co. durch ihr häufig starres Material die Zecke oft quetschen oder verletzen, greift der tickSAFE Zeckengreifer die Zecke sanft und diese kann dann langsam herausged

In [14]:
######################################### TO COMBINE Nährwertangaben & Vitamin / Mineral keys ###############################################

# Iterate through each item in the all_attrs_cosmetic list
for item in all_attrs_cosmetic:
    # Check if the item contains both 'Nährwertangaben' and 'Vitamin / Mineral' keys
    if 'Nährwertangaben' in item and 'Vitamin / Mineral' in item:
        # Combine the values of 'Nährwertangaben' and 'Vitamin / Mineral' into a new 'nutriments' key
        item['nutriments'] = item['Nährwertangaben'] + '. ' + item['Vitamin / Mineral']
        # Remove the 'Nährwertangaben' key from the item
        del item['Nährwertangaben']
        # Remove the 'Vitamin / Mineral' key from the item
        del item['Vitamin / Mineral']


In [15]:
###################################### TO APPEND Artikelinformationen's values TO THE description key #############################################

for item in all_attrs_cosmetic:
    if 'description' in item and 'Artikelinformationen' in item:
        # Append Artikelinformationen value to Description
        item['description'] = item.get('description', '') + ' ' + item.get('Artikelinformationen', '')
        # Delete the Artikelinformationen key
        del item['Artikelinformationen']

In [16]:
################################################### TO RE-ORDER THE KEY'S PLACE #####################################################

# Iterate through each dictionary in the all_attrs_cosmetic list
for attr in all_attrs_cosmetic:
    # Check if the dictionary contains the 'nutriments' key
    if 'nutriments' in attr:
        # Find the index of the 'labels' key
        labels_index = list(attr.keys()).index('labels')
        # Remove the 'nutriments' key-value pair from the dictionary and store the value
        attr['nutriments'] = attr.pop('nutriments')
        # Convert the dictionary into a list of tuples (key-value pairs)
        attr_items = list(attr.items())
        # Move the 'nutriments' key-value pair to the position right after the 'labels' key
        attr_items.insert(labels_index + 1, attr_items.pop(-1))
        # Clear the original dictionary
        attr.clear()
        # Update the dictionary with the reordered key-value pairs
        attr.update(attr_items)


In [17]:
############################################# SAVING COSMETIC PRODUCTS IN A .JSON FILE ################################################

with open('netto_cosmetic_products.json', 'w', encoding='utf-8') as json_file:
    json.dump(all_attrs_cosmetic, json_file, ensure_ascii=False, indent=4)

In [18]:
############################################# COMBINING THE FOODS AND THE COSMETIC PRODUCTS DATA OF NETTO #####################################

all_netto_attrs = all_attrs + all_attrs_cosmetic

In [19]:
############################################# SAVING ALL PRODUCTS IN A .JSON FILE ################################################

with open('netto_products.json', 'w', encoding='utf-8') as json_file:
    json.dump(all_netto_attrs, json_file, ensure_ascii=False, indent=4)

In [20]:
############################################# SAVING ALL PRODUCTS IN A .CSV FILE ################################################

# Determine all possible keys
all_keys = set()
for dictionary in all_netto_attrs:
    all_keys.update(dictionary.keys())

# Create a new list of dictionaries with all keys
updated_attrs = []
for dictionary in all_netto_attrs:
    new_dict = {key: dictionary.get(key, '') for key in all_keys}
    updated_attrs.append(new_dict)

# Save the new list of dictionaries to a CSV file
with open("netto_products.csv", 'w', newline='', encoding='utf-8') as csv_file:
    writer = csv.DictWriter(csv_file, fieldnames=all_keys)
    writer.writeheader()
    writer.writerows(updated_attrs)